In [ ]:
import numpy as np
import pandas as pd
import nltk
from nltk.translate.bleu_score import sentence_bleu
import os, json, gc, re, random
from tqdm.notebook import tqdm
from sklearn.model_selection import train_test_split

import matplotlib.pyplot as plt
%matplotlib inline
import plotly.express as px
import seaborn as sns

import warnings
warnings.filterwarnings("ignore")

import logging
logging.basicConfig(level=logging.INFO)
transformers_logger = logging.getLogger("transformers")
transformers_logger.setLevel(logging.WARNING)
from google.colab import drive

In [ ]:
drive.mount('/content/gdrive')

Mounted at /content/gdrive


In [ ]:
veri=pd.read_excel("/content/gdrive/My Drive/TezSonCalismalar/DataFindingsImpression.xlsx")

In [ ]:
veri.head()

Unnamed: 0                                           findings  \
0           0  PA and lateral views of the chest provided.   ...   
1           1  As compared to the prior examination dated ___...   
2           3  A triangular opacity in the right lung apex is...   
3           4  Mild to moderate enlargement of the cardiac si...   
4           5  There is mild pulmonary edema with superimpose...   

                                          impression  
0                    No acute intrathoracic process.  
1      No evidence of acute cardiopulmonary process.  
2  Right upper lobe pneumonia or mass.  However, ...  
3            No radiographic evidence for pneumonia.  
4  Mild pulmonary edema with superimposed left up...

In [ ]:
%%time

!pip install torch

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
CPU times: user 42.8 ms, sys: 5.31 ms, total: 48.1 ms
Wall time: 5.42 s


In [ ]:
%%time

!pip install tokenizer

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 79.1/79.1 kB 9.0 MB/s eta 0:00:00
CPU times: user 44.1 ms, sys: 6.62 ms, total: 50.8 ms
Wall time: 5.34 s


In [ ]:
%%time

!pip install transformers

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.2/7.2 MB 72.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 236.8/236.8 kB 28.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 72.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 51.1 MB/s eta 0:00:00
CPU times: user 157 ms, sys: 26 ms, total: 182 ms
Wall time: 24.4 s


In [ ]:
%%time

!pip install simpletransformers

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 250.7/250.7 kB 11.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 485.6/485.6 kB 40.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.6/43.6 kB 5.3 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 64.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.9/8.9 MB 44.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 21.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 184.3/184.3 kB 8.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 206.7/206.7 kB 11.4 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 110.5/110.5 kB 13.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.5/212.5 kB 17.5 MB/s eta 0:00:00
     ━━━━━━━━━━━

In [ ]:
import torch, transformers, tokenizers
torch.__version__, transformers.__version__, tokenizers.__version__

('2.0.1+cu118', '4.30.2', '0.13.3')

In [ ]:
veri.head()

Unnamed: 0                                           findings  \
0           0  PA and lateral views of the chest provided.   ...   
1           1  As compared to the prior examination dated ___...   
2           3  A triangular opacity in the right lung apex is...   
3           4  Mild to moderate enlargement of the cardiac si...   
4           5  There is mild pulmonary edema with superimpose...   

                                          impression  
0                    No acute intrathoracic process.  
1      No evidence of acute cardiopulmonary process.  
2  Right upper lobe pneumonia or mass.  However, ...  
3            No radiographic evidence for pneumonia.  
4  Mild pulmonary edema with superimposed left up...

In [ ]:
veri = veri.drop(['Unnamed: 0'], axis=1)

In [ ]:
veri.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 36717 entries, 0 to 36716
Data columns (total 2 columns):
 #   Column      Non-Null Count  Dtype 
---  ------      --------------  ----- 
 0   findings    36717 non-null  object
 1   impression  36717 non-null  object
dtypes: object(2)
memory usage: 573.8+ KB


In [ ]:
veri = veri.dropna()

In [ ]:
veri.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 36717 entries, 0 to 36716
Data columns (total 2 columns):
 #   Column      Non-Null Count  Dtype 
---  ------      --------------  ----- 
 0   findings    36717 non-null  object
 1   impression  36717 non-null  object
dtypes: object(2)
memory usage: 573.8+ KB


In [ ]:
veri.columns = ['input_text', 'target_text']
veri

input_text  \
0      PA and lateral views of the chest provided.   ...   
1      As compared to the prior examination dated ___...   
2      A triangular opacity in the right lung apex is...   
3      Mild to moderate enlargement of the cardiac si...   
4      There is mild pulmonary edema with superimpose...   
...                                                  ...   
36712  A right-sided Port-A-Cath_x000D_\n terminates ...   
36713  There is no evidence of pneumothorax or displa...   
36714  The lungs are clear without focal consolidatio...   
36715  SUSPECT BACKGROUND HYPERINFLATION, AS CAN BE S...   
36716  Frontal and lateral chest radiographs demonstr...   

                                             target_text  
0                        No acute intrathoracic process.  
1          No evidence of acute cardiopulmonary process.  
2      Right upper lobe pneumonia or mass.  However, ...  
3                No radiographic evidence for pneumonia.  
4      Mild pulmonary edema with superimposed left up...  
...                                                  ...  
36712                    No acute intrathoracic process.  
36713  No evidence of pneumothorax or displaced rib f...  
36714                  No acute cardiopulmonary process.  
36715  NO ACUTE PULMONARY PROCESS IDENTIFIED.  NO PNE...  
36716                 Hyperexpansion.  No consolidation.  

[36717 rows x 2 columns]

In [ ]:
%%time

from simpletransformers.seq2seq import Seq2SeqModel

eval_df = veri.sample(frac=0.1, random_state=42)
train_df = veri.drop(eval_df.index)

model_args = {
    "reprocess_input_data": True,
    "overwrite_output_dir": True,
    "save_model_every_epoch": False,
    "save_eval_checkpoints": False,
    "max_seq_length": 512,
    "train_batch_size": 8,
    "num_train_epochs": 2,
    "use_multiprocessing": False,
    "truncation": True,
    "tokenizer": True,
}

from transformers import AutoTokenizer, AutoModelForSeq2SeqLM

tokenizer = AutoTokenizer.from_pretrained("algoprog/mimics-query-bart-base")

#model = AutoModelForSeq2SeqLM.from_pretrained("algoprog/mimics-query-bart-base")

#Create a Bart-base model
model = Seq2SeqModel(encoder_decoder_type="bart",
                   encoder_decoder_name="algoprog/mimics-query-bart-base",
                    args=model_args)

CPU times: user 6.58 s, sys: 1.95 s, total: 8.53 s
Wall time: 23.1 s


In [ ]:
train_df

input_text  \
0      PA and lateral views of the chest provided.   ...   
1      As compared to the prior examination dated ___...   
2      A triangular opacity in the right lung apex is...   
3      Mild to moderate enlargement of the cardiac si...   
5      The lungs are clear of consolidation, effusion...   
...                                                  ...   
36711  There are bibasilar opacities, which_x000D_\n ...   
36712  A right-sided Port-A-Cath_x000D_\n terminates ...   
36713  There is no evidence of pneumothorax or displa...   
36714  The lungs are clear without focal consolidatio...   
36715  SUSPECT BACKGROUND HYPERINFLATION, AS CAN BE S...   

                                             target_text  
0                        No acute intrathoracic process.  
1          No evidence of acute cardiopulmonary process.  
2      Right upper lobe pneumonia or mass.  However, ...  
3                No radiographic evidence for pneumonia.  
5                      No acute cardiopulmonary process.  
...                                                  ...  
36711  Bibasilar opacities, possible effusions and at...  
36712                    No acute intrathoracic process.  
36713  No evidence of pneumothorax or displaced rib f...  
36714                  No acute cardiopulmonary process.  
36715  NO ACUTE PULMONARY PROCESS IDENTIFIED.  NO PNE...  

[33045 rows x 2 columns]

In [ ]:
%%time

# Train the model
model.train_model(train_df)

# Evaluate the model
result = model.eval_model(eval_df)

  0%|          | 0/33045 [00:00<?, ?it/s]

Epoch:   0%|          | 0/2 [00:00<?, ?it/s]

Running Epoch 0 of 2:   0%|          | 0/4131 [00:00<?, ?it/s]

Running Epoch 1 of 2:   0%|          | 0/4131 [00:00<?, ?it/s]

  0%|          | 0/3672 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/459 [00:00<?, ?it/s]

CPU times: user 1h 16min 37s, sys: 26.4 s, total: 1h 17min 4s
Wall time: 1h 19min


In [ ]:
print(result)

{'eval_loss': 0.05776997811662151}


In [ ]:
eval_df

input_text  \
12966  Cardiac, mediastinal and hilar contours are no...   
13614  The heart size is top normal with mildly tortu...   
28573  Relatively low lung volumes are seen.  There i...   
2265   PA and lateral views of the chest provided. Th...   
842    There is again a mild interstitial abnormality...   
...                                                  ...   
10373  The cardiomediastinal silhouettes are stable a...   
20027  The lungs are clear without focal consolidatio...   
20547  The cardiac, mediastinal and hilar_x000D_\n co...   
19316  Heart size and cardiomediastinal contours are ...   
9469   The lungs are well expanded and clear.  Cardio...   

                                             target_text  
12966  No acute cardiopulmonary abnormality.  No disp...  
13614                    No acute intrathoracic process.  
28573  Right lower lobe consolidation compatible with...  
2265                     No acute intrathoracic process.  
842    Findings suggesting slight pulmonary vascular ...  
...                                                  ...  
10373  Stable appearance of the heart and lungs.  No ...  
20027                  No acute cardiopulmonary process.  
20547                           Normal chest radiograph.  
19316                   No evidence of pneumoperitoneum.  
9469        Unremarkable chest radiographic examination.  

[3672 rows x 2 columns]

In [ ]:
cols = ['True Impression', 'Predicted Impression']
lst = []

In [ ]:
test_df = eval_df.sample(n=400)
outputdata = pd.DataFrame()
for idx, row in test_df.iterrows():

    findings = row['input_text']
    true_impression = row['target_text']

    # Predict with trained BART model
    predicted_impression = model.predict([findings])[0]
    lst.append([true_impression,predicted_impression])

    print(f'True Impression: {true_impression}\n')
    print(f'Predicted Impression: {predicted_impression}\n')
    print(f'Findings: {findings}\n\n\n')

Generating outputs:   0%|          | 0/1 [00:00<?, ?it/s]

True Impression: Small right pneumothorax without evidence of tension.

Predicted Impression: Small right pneumothorax without significant change.

Findings: AP portable upright and lateral views the chest provided.  As seen on prior_x000D_
 exam, there is a small right pneumothorax without significant right lung_x000D_
 collapse or shift of midline structures.  There is a small right pleural_x000D_
 effusion also noted.  Large paraseptal blebs noted at the left lung base. _x000D_
 Cardiomediastinal silhouette appears normal.  Chronic left clavicular_x000D_
 deformity noted.  Otherwise the bony structures appear intact.





Generating outputs:   0%|          | 0/1 [00:00<?, ?it/s]

True Impression: Left chest tube to this is unchanged. No pneumothorax.

Predicted Impression: No significant change from the prior examination.

Findings: Single AP view of the chest provided._x000D_
 _x000D_
 No significant changes from the prior examination. Mild atelectatic change in_x000D_
 the left lung base._x000D_
 _x000D_
 No pleural effusion, no pneumothorax. Left chest tube position is unchanged_x000D_
 ending in the apex of the left hemi thorax.





Generating outputs:   0%|          | 0/1 [00:00<?, ?it/s]

...

True Impression: 1. No pneumothorax detected._x000D_
 2. Cardiomegaly and CHF again noted._x000D_
 3. Increased retrocardiac density, consistent with left lower lobe collapse_x000D_
 and/or consolidation and possible small left effusion is similar to the prior_x000D_
 film.

Predicted Impression: No significant interval change.

Findings: Compared with ___, I doubt significant interval change._x000D_
 _x000D_
 Again seen is a right IJ central line tip over distal SVC.  No pneumothorax is_x000D_
 detected._x000D_
 _x000D_
 Again seen is cardiomegaly with sternotomy wires, similar to prior, allowing_x000D_
 for differences in positioning.  Platelike atelectasis the left upper zone,_x000D_
 increased retrocardiac density, possible small left effusion are again seen. _x000D_
 Upper zone redistribution with vascular plethora and vascular blurring_x000D_
 suggestive of CHF again noted.





Generating outputs:   0%|          | 0/1 [00:00<?, ?it/s]

True Impression: 1.  Chronic pulmonary vascular congestion, slightly more congested since_x000D_
 ___ yet unchanged from prior examination._x000D_
 _x000D_
 2.  Unchanged small right pleural effusion.

Predicted Impression: 1.  No significant change since yesterday._x000D_
 2. 

Findings: As compared to prior chest radiograph from ___, there has_x000D_
 been no significant change. Pulmonary vascular congestion is chronic. Lungs_x000D_
 appears slightly more congested since ___ but unchanged from_x000D_
 yesterday.  Moderate cardiomegaly is stable.  There are asbestos-related_x000D_
 calcified pleural plaques. A small right pleural effusion is unchanged. There_x000D_
 is no pneumothorax. Tip of the right internal jugular line is at the level of_x000D_
 the superior cavoatrial junction.





Generating outputs:   0%|          | 0/1 [00:00<?, ?it/s]

True Impression: Left lower lobe patchy opacity concerning for pneumonia.  Followup radiographs_x000D_
 after treatment are recommended to ensure resolution of this finding.

Predicted Impression: Patchy left lower lobe opacity is concerning for pneumonia.

Findings: The cardiac, mediastinal and hilar contours are normal.  The pulmonary_x000D_
 vasculature is not engorged.  Patchy left lower lobe opacity is concerning for_x000D_
 pneumonia.  No pleural effusion or pneumothorax is seen.  Remote left-sided_x000D_
 rib fractures are again seen.





In [ ]:
outputdata = pd.DataFrame(lst,columns=cols)
outputdata

True Impression  \
0    Small right pneumothorax without evidence of t...   
1    Left chest tube to this is unchanged. No pneum...   
2          right apical pneumothorax increased in size   
3    1. New endotracheal tube ends ___.7 cm from th...   
4    No significant interval change compared to the...   
..                                                 ...   
395              No acute cardiopulmonary abnormality.   
396  Interval improvement in the right basilar opac...   
397  1. No pneumothorax detected._x000D_\n 2. Cardi...   
398  1.  Chronic pulmonary vascular congestion, sli...   
399  Left lower lobe patchy opacity concerning for ...   

                                  Predicted Impression  
0    Small right pneumothorax without significant c...  
1    No significant change from the prior examination.  
2    Increased size of large right apical pneumotho...  
3    1.  New endotracheal tube ends ___.7 cm from t...  
4                    No acute cardiopulmonary process.  
..                                                 ...  
395              No acute cardiopulmonary abnormality.  
396  Interval improvement in right basilar opacity ...  
397                    No significant interval change.  
398  1.  No significant change since yesterday._x00...  
399  Patchy left lower lobe opacity is concerning f...  

[400 rows x 2 columns]

In [ ]:
bleu_scores = []
for index, row in outputdata.iterrows():
    predicted_impression = row["Predicted Impression"]
    true_impression = row["True Impression"]
    bleu_score = sentence_bleu([true_impression], predicted_impression, weights=(0.5, 0.5))
    bleu_scores.append(bleu_score)

In [ ]:
average_bleu_score = sum(bleu_scores) / len(bleu_scores)

In [ ]:
print("Ortalama BLEU Skoru:", average_bleu_score)

Ortalama BLEU Skoru: 0.4316929990359567


In [ ]:
import locale
def getpreferredencoding(do_setlocale = True):
    return "UTF-8"
locale.getpreferredencoding = getpreferredencoding

In [ ]:
%time

!pip install rouge

CPU times: user 4 µs, sys: 0 ns, total: 4 µs
Wall time: 6.91 µs
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
from rouge import Rouge
def compute_rouge(predictions, targets):
    predictions = [" ".join(prediction).lower() for prediction in predictions]
    predictions = [prediction if prediction else "EMPTY" for prediction in predictions]
    targets = [" ".join(target).lower() for target in targets]
    targets = [target if target else "EMPTY" for target in targets]
    rouge = Rouge()
    scores = rouge.get_scores(hyps=predictions, refs=targets, avg=True)
    return scores['rouge-2']['f']

In [ ]:
compute_rouge(outputdata["Predicted Impression"], outputdata["True Impression"])

0.5506840092239037

In [ ]:
nltk.download('punkt')

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


True

In [ ]:
outputdata.to_excel("TemizStopWordsBartFacebookToken2Epoch.xlsx")

In [ ]:
from google.colab import files
files.download("TemizStopWordsBartFacebookToken2Epoch.xlsx")

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>